In [1]:
# Importing libs and your features

from concurrent.futures import ThreadPoolExecutor
import json
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.by import By

# Imports below will be to update the ChromeDriverManager to new version

from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.service import Service 

service =  Service(ChromeDriverManager().install())

### Getting page lenght

In [2]:
# Start the driver
driver = webdriver.Chrome(service=service)

driver.get('https://www.metacritic.com/browse/game/?releaseYearMin=1910&releaseYearMax=2023&page=1')

element = driver.find_element(By.XPATH, '//*[@id="__layout"]/div/div[2]/div[1]/main/section/div[4]/span[2]/span[4]/span/span/span')

pages_len = (element.text).replace(',','')
pages_len = int(pages_len)


In [3]:
### have 803 pages with metascore

In [4]:
pagesList = []

for i in range(1, pages_len):
    pagesList.append(f'https://www.metacritic.com/browse/games/score/metascore/all/all/filtered?page={i}')


In [5]:
pagesList = []

for i in range(1, 100):
    pagesList.append(f'https://www.metacritic.com/browse/games/score/metascore/all/all/filtered?page={i}')

In [20]:
# Here will be links collect from the page of each game

driver = webdriver.Chrome(service=service)

linkList = []
def link_collect(page):
    driver.get(page)
    for i in range(1,4,2):
        for j in range(1,13):
            link = driver.find_element(By.XPATH, f'//*[@id="__layout"]/div/div[2]/div[1]/main/section/div[3]/div[{i}]/div[{j}]/a').get_attribute('href')
            linkList.append(link)  
    
with ThreadPoolExecutor(max_workers=3) as executor:
    for page in pagesList:
        executor.submit(link_collect, page)
        
driver.quit()

2023-09-21 19:16:00 [selenium.webdriver.common.service] DEBUG: Started executable: `C:\Users\Admin\.wdm\drivers\chromedriver\win64\117.0.5938.92\chromedriver-win32/chromedriver.exe` in a child process with pid: 26144
2023-09-21 19:16:00 [selenium.webdriver.remote.remote_connection] DEBUG: POST http://localhost:49694/session {"capabilities": {"firstMatch": [{}], "alwaysMatch": {"browserName": "chrome", "pageLoadStrategy": "normal", "goog:chromeOptions": {"extensions": [], "args": []}}}}
2023-09-21 19:16:00 [urllib3.connectionpool] DEBUG: Starting new HTTP connection (1): localhost:49694
2023-09-21 19:16:01 [urllib3.connectionpool] DEBUG: http://localhost:49694 "POST /session HTTP/1.1" 200 883
2023-09-21 19:16:01 [selenium.webdriver.remote.remote_connection] DEBUG: Remote response: status=200 | data={"value":{"capabilities":{"acceptInsecureCerts":false,"browserName":"chrome","browserVersion":"117.0.5938.92","chrome":{"chromedriverVersion":"117.0.5938.92 (67649b10b92bb182fba357831ef7dd6a1

In [7]:
# Colleting links of page 201 of games

driver.get('https://www.metacritic.com/browse/games/score/metascore/all/all/filtered?page=200')

for i in range(2,10,2):
    for j in range(1,10,2):   
        link = driver.find_element(By.XPATH, f'//*[@id="main_content"]/div[1]/div[2]/div/div[1]/div/div[{i}]/table/tbody/tr[{j}]/td[2]/a').get_attribute('href')
        linkList.append(link) 

with open('gamesLinkList.txt', 'w') as file:
    for item in linkList:
        file.write(f"{item}\n")

In [27]:
# Inserting content linkList.txt on list

with open("linkList.txt", "r") as file:
    lines = file.readlines()

links = list(lines)

In [76]:
# Function created for data collect of games pages
# Collecting title, release, game plataform, metascore, game critic reviews, use score, ratings numbers, game developer, game genre(s) and players numbers 

# OBS: change name numbers ratings for rating numbers

def info_collecting(url):
    
    game_data_dict = {}

    driver.get(url)

    # Collecting game title
    try:
        title = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[1]/div[2]/a/h1').text
        game_data_dict['title'] = title
    except Exception:
        game_data_dict['title'] = None

    # Collecting game release
    try:
        release = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[1]/div[3]/ul/li[2]/span[2]').text
        game_data_dict['release'] = release
    except Exception:
        game_data_dict['release']= None

    # Collecting game plataform
    try:
        plataform = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[1]/div[2]/span').text
        game_data_dict['plataform'] = plataform
    except Exception:
        game_data_dict['plataform'] = None

    # Collecting game metascore
    try:
        metascore = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[1]/div[1]/div/div/a/div/span').text
        game_data_dict['metascore'] = metascore
    except Exception:
        metascore = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[1]/div[1]/div/div/a/div/span').text
        game_data_dict['metascore'] = metascore

    # Collecting game critict reviews (metascore is based on critic reviews)
    try:
        critic_reviews = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[1]/div[1]/div/div/div[2]/p/span[2]/a/span').text
        game_data_dict['critic_reviews'] = critic_reviews
    except Exception:
        critic_reviews = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[1]/div[1]/div/div/div[2]/p/span[2]/a/span').text
        game_data_dict['critic_reviews'] = critic_reviews

    # Collecting user score
    try:
        user_score = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[1]/div[2]/div[1]/div/a/div').text
        game_data_dict['user_score'] = user_score
    except Exception:
        user_score = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[1]/div[2]/div[1]/div/a/div').text
        game_data_dict['user_score'] = user_score

    # Collecting numbers ratings (user score is based on number ratings)
    try:
        numbers_ratings = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[1]/div[2]/div[1]/div/div[2]/p/span[2]/a').text
        game_data_dict['numbers_ratings'] = numbers_ratings
    except Exception:
        numbers_ratings = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[1]/div[2]/div[1]/div/div[2]/p/span[2]/a').text
        game_data_dict['numbers_ratings'] = numbers_ratings

    # Collecting game developer
    try:
        developer = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[2]/div[2]/ul/li[1]/span[2]/a').text
        game_data_dict['developer'] = developer
    except Exception:
        developer = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[2]/div[2]/ul/li[1]/span[2]/a').text
        game_data_dict['developer'] = developer

    # Collecting game genre(s)
    try:
        genres = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[2]/div[2]/ul/li[2]').text
        game_data_dict['genre(s)'] = genres
    except Exception:
        genres = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[2]/div[2]/ul/li[2]').text
        game_data_dict['genre(s)'] = genres

    # Collecting players number
    try:
        players_number = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div/div[2]/div[2]/div[2]/ul/li[3]/span[2]').text
        game_data_dict['players_number'] = players_number
    except Exception:
        players_number = driver.find_element(By.XPATH, '//*[@id="main"]/div/div[1]/div[1]/div[3]/div/div[2]/div[2]/div[2]/ul/li[3]/span[2]').text
        game_data_dict['players_number'] = players_number

    return game_data_dict

In [85]:
# On March 3nd, 2023, Metacritic displayed 20,021 evaluated games.

game_data_list = []

for i in links: 
    try:
        game_data_list.append(info_collecting(i))
    except NoSuchElementException:
        pass
    
with open('gamesInfo.json', 'w') as arq:
    json.dump(game_data_list, arq, indent=2)

In [2]:
# End the driver

driver.quit()